In [99]:
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objs as go
from plotly.subplots import make_subplots
from scipy.fft import fft, ifft

def generate_water_flow_data(days=365, leak_prob=0.005, leak_pres_drop=(5, 10), leak_flow_drop=(10, 20)):
    # Generate a time range with hourly frequency for one year
    time_range = pd.date_range(start='1/1/2023', periods=days * 24, freq='h')

    # Create base data with daily, weekly, and seasonal cycles
    daily_cycle = np.sin(np.linspace(0, 2 * np.pi, 24))
    weekly_cycle = np.sin(np.linspace(0, 2 * np.pi, 7 * 24))
    seasonal_temps = [10, 12, 18, 25, 32, 40, 35, 33, 30, 25, 20, 15]  # Adjusted range from 10 to 40
    seasonal_cycle = np.interp(np.linspace(1, 12, days * 24), np.arange(1, 13), seasonal_temps)

    # Generate the data
    temperature = []
    pressure = []
    flow_rate = []
    anomaly_detection = []
    leak_detection = []

    for i in range(days * 24):
        daily_value = daily_cycle[i % 24]
        weekly_value = weekly_cycle[i % (7 * 24)]
        seasonal_value = seasonal_cycle[i]
        
        temp = seasonal_value + daily_value + weekly_value + np.random.normal(0, 1)
        pres = 50 + 0.5 * (daily_value + weekly_value) + 0.1 * (seasonal_value - np.mean(seasonal_temps)) + np.random.normal(0, 0.5)
        flow = 100 + 2 * (daily_value + weekly_value) + 0.5 * (seasonal_value - np.mean(seasonal_temps)) + np.random.normal(0, 2)
        
        # Simulate random anomalies and leaks
        if np.random.random() < leak_prob:
            pres_anomaly = pres - np.random.uniform(*leak_pres_drop)
            flow_anomaly = flow - np.random.uniform(*leak_flow_drop)
            if pres_anomaly < 45 and flow_anomaly < 90:  # Example thresholds for detecting a leak
                pres = pres_anomaly
                flow = flow_anomaly
                leak_detection.append(1)  # Indicate a leak
                anomaly_detection.append(1)  # Indicate an anomaly (also a leak in this case)
            else:
                anomaly_detection.append(1)  # Indicate a normal anomaly
                leak_detection.append(0)  # Not a leak
        else:
            anomaly_detection.append(0)  # No anomaly
            leak_detection.append(0)  # No leak
        
        temperature.append(temp)
        pressure.append(pres)
        flow_rate.append(flow)

    # Apply Fourier transform and inverse Fourier transform to smoothen the data
    def smooth_data(data):
        fft_data = fft(data)
        # Zero out high-frequency components (keep only 10% of the frequencies)
        fft_data[int(len(fft_data) * 0.1):] = 0
        smoothed_data = ifft(fft_data).real
        return smoothed_data

    temperature_smoothed = smooth_data(temperature)
    pressure_smoothed = smooth_data(pressure)
    flow_rate_smoothed = smooth_data(flow_rate)

    # Convert data to a Pandas DataFrame
    df = pd.DataFrame({
        'Timestamp': time_range,
        'Temperature': temperature_smoothed,
        'Pressure': pressure_smoothed,
        'Flow_Rate': flow_rate_smoothed,
        'Anomaly_Detection': anomaly_detection,
        'Leak_Detection': leak_detection
    })
    df.set_index('Timestamp', inplace=True)
    
    return df

# Generate data
df = generate_water_flow_data()

# Create subplots for better visualization
fig = make_subplots(rows=3, cols=1, shared_xaxes=True, subplot_titles=('Temperature', 'Pressure', 'Flow Rate'))

# Temperature plot
fig.add_trace(go.Scatter(x=df.index, y=df['Temperature'], mode='lines', name='Temperature'), row=1, col=1)

# Pressure plot with anomaly and leak detection
fig.add_trace(go.Scatter(x=df.index, y=df['Pressure'], mode='lines', name='Pressure'), row=2, col=1)
anomaly_points_pres = df[df['Anomaly_Detection'] == 1]
leak_points_pres = df[df['Leak_Detection'] == 1]
fig.add_trace(go.Scatter(x=anomaly_points_pres.index, y=anomaly_points_pres['Pressure'], mode='markers', name='Anomaly Detected', marker=dict(color='purple')), row=2, col=1)
fig.add_trace(go.Scatter(x=leak_points_pres.index, y=leak_points_pres['Pressure'], mode='markers', name='Leak Detected', marker=dict(color='green')), row=2, col=1)

# Flow rate plot with anomaly and leak detection
fig.add_trace(go.Scatter(x=df.index, y=df['Flow_Rate'], mode='lines', name='Flow Rate'), row=3, col=1)
anomaly_points_flow = df[df['Anomaly_Detection'] == 1]
leak_points_flow = df[df['Leak_Detection'] == 1]
fig.add_trace(go.Scatter(x=anomaly_points_flow.index, y=anomaly_points_flow['Flow_Rate'], mode='markers', name='Anomaly Detected', marker=dict(color='purple')), row=3, col=1)
fig.add_trace(go.Scatter(x=leak_points_flow.index, y=leak_points_flow['Flow_Rate'], mode='markers', name='Leak Detected', marker=dict(color='green')), row=3, col=1)

fig.update_layout(height=900, width=1200, title_text='Water Flow Data with Anomaly and Leak Detection', showlegend=True)
fig.show()

# Export data to CSV
df.to_csv('water_flow_data_with_anomaly_leak_old.csv')


In [110]:
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objs as go
from plotly.subplots import make_subplots
from scipy.fft import fft, ifft

def generate_water_flow_data(years=2, days=365, leak_prob=0.005, leak_pres_drop=(2, 5), leak_flow_drop=(1, 3)):
    # Generate a time range with hourly frequency for the specified number of years
    time_range = pd.date_range(start='1/1/2023', periods=years * days * 24, freq='h')

    # Create base data with daily, weekly, and seasonal cycles using polynomial functions and randomness
    daily_cycle = np.poly1d([0.1, -0.2, 0.5])(np.linspace(-1, 1, 24)) + np.random.normal(0, 0.05, 24)
    weekly_cycle = np.poly1d([-0.1, 0.3, 0.1])(np.linspace(-1, 1, 7 * 24)) + np.random.normal(0, 0.1, 7 * 24)
    seasonal_temps = [15, 18, 22, 28, 35, 38, 34, 32, 30, 26, 21, 16]   # Adjusted range from 10 to 40
    seasonal_cycle = np.tile(np.interp(np.linspace(1, 12, days * 24), np.arange(1, 13), seasonal_temps), years)

    # Generate the data
    temperature = []
    pressure = []
    flow_rate = []
    anomaly_detection = []
    leak_detection = []

    for i in range(years * days * 24):
        daily_value = daily_cycle[i % 24]
        weekly_value = weekly_cycle[i % (7 * 24)]
        seasonal_value = seasonal_cycle[i]
        
        temp = seasonal_value + daily_value + weekly_value + np.random.normal(0, 1)
        pres = 20 + 5 * (daily_value + weekly_value) + 0.5 * (seasonal_value - np.mean(seasonal_temps)) + np.random.normal(0, 0.5)
        pres = np.clip(pres, 10, 30)  # Ensuring pressure stays within the range
        flow = 5 + 2 * (daily_value + weekly_value) + 0.1 * (seasonal_value - np.mean(seasonal_temps)) + np.random.normal(0, 0.5)
        flow = np.clip(flow, 1, 10)  # Ensuring flow rate stays within the range
        
        # Simulate random anomalies and leaks
        if np.random.random() < leak_prob:
            pres_anomaly = pres - np.random.uniform(*leak_pres_drop)
            flow_anomaly = flow - np.random.uniform(*leak_flow_drop)
            if pres_anomaly < 45 and flow_anomaly < 90:  # Example thresholds for detecting a leak
                pres = pres_anomaly
                flow = flow_anomaly
                leak_detection.append(1)  # Indicate a leak
                anomaly_detection.append(1)  # Indicate an anomaly (also a leak in this case)
            else:
                anomaly_detection.append(1)  # Indicate a normal anomaly
                leak_detection.append(0)  # Not a leak
        else:
            anomaly_detection.append(0)  # No anomaly
            leak_detection.append(0)  # No leak
        
        temperature.append(temp)
        pressure.append(pres)
        flow_rate.append(flow)

    # Apply Fourier transform and inverse Fourier transform to smoothen the data
    def smooth_data(data):
        fft_data = fft(data)
        # Zero out high-frequency components (keep only 10% of the frequencies)
        fft_data[int(len(fft_data) * 0.1):] = 0
        smoothed_data = ifft(fft_data).real
        return smoothed_data

    temperature_smoothed = smooth_data(temperature)
    pressure_smoothed = smooth_data(pressure)
    flow_rate_smoothed = smooth_data(flow_rate)

    # Convert data to a Pandas DataFrame
    df = pd.DataFrame({
        'Timestamp': time_range,
        'Temperature': temperature_smoothed,
        'Pressure': pressure_smoothed,
        'Flow_Rate': flow_rate_smoothed,
        'Anomaly_Detection': anomaly_detection,
        'Leak_Detection': leak_detection
    })
    df.set_index('Timestamp', inplace=True)
    
    return df

# Generate water flow data for 2 years
df = generate_water_flow_data()
df.to_csv('water_flow_data_with_anomaly_leak.csv')

# Load ambient temperature data (simulated or actual)
ambient_temp_file = 'simulated_hourly_temperature.csv'  # Path to the previously saved ambient temperature data
ambient_df = pd.read_csv(ambient_temp_file)

# Check if the flow rate and ambient temperature data have the same length
if len(df) != len(ambient_df):
    raise ValueError("The length of the flow rate data and the ambient temperature data must match.")

# Assuming 'Flow_Rate' column contains the water flow rates (units) and is in the same order as ambient temperature
flow_rate = df['Flow_Rate'].values  # Water flow rate (units)
ambient_temperature = ambient_df['Hourly Temperature (°C)'].values  # Ambient temperature (°C)

# Initialize the water temperature inside the pipe
initial_water_temp = 27.0  # Initial water temperature in the pipe (°C)
water_temperature = np.zeros_like(ambient_temperature)  # Array to store water temperature
water_temperature[0] = initial_water_temp  # Start with the initial temperature

# Define heat transfer coefficient (alpha) and flow factor
alpha = 0.1  # Heat transfer coefficient, controls how quickly the water temperature responds to ambient temperature
flow_factor = flow_rate / np.max(flow_rate)  # Normalize the flow rate to range between 0 and 1

# Simulate the water temperature using Euler's method for numerical integration
for i in range(1, len(ambient_temperature)):
    # Calculate the rate of change of the water temperature
    delta_temp = alpha * (ambient_temperature[i] - water_temperature[i - 1]) * flow_factor[i - 1]
    
    # Update the water temperature using Euler's method (forward time step)
    water_temperature[i] = water_temperature[i - 1] + delta_temp

# Save the simulated water temperature data to a new CSV file
output_df = pd.DataFrame({
    'Timestamp': df.index,  # Use the same Timestamp as the water flow data
    'Water Temperature (°C)': water_temperature
})

# Save the data to CSV
output_df.to_csv('simulated_water_temperature.csv', index=False)

# Create subplots for better visualization of flow data
fig = make_subplots(rows=3, cols=1, shared_xaxes=True, subplot_titles=('Water Temperature', 'Pressure', 'Flow Rate'))

# Water Temperature plot
# Water Temperature plot
fig.add_trace(go.Scatter(x=df.index, y=water_temperature, mode='lines', name='Water Temperature'), row=1, col=1)

# Pressure plot with anomaly and leak detection
fig.add_trace(go.Scatter(x=df.index, y=df['Pressure'], mode='lines', name='Pressure'), row=2, col=1)
anomaly_points_pres = df[df['Anomaly_Detection'] == 1]
leak_points_pres = df[df['Leak_Detection'] == 1]
fig.add_trace(go.Scatter(x=anomaly_points_pres.index, y=anomaly_points_pres['Pressure'], mode='markers', name='Anomaly Detected', marker=dict(color='purple')), row=2, col=1)
fig.add_trace(go.Scatter(x=leak_points_pres.index, y=leak_points_pres['Pressure'], mode='markers', name='Leak Detected', marker=dict(color='green')), row=2, col=1)

# Flow rate plot with anomaly and leak detection
fig.add_trace(go.Scatter(x=df.index, y=df['Flow_Rate'], mode='lines', name='Flow Rate'), row=3, col=1)
anomaly_points_flow = df[df['Anomaly_Detection'] == 1]
leak_points_flow = df[df['Leak_Detection'] == 1]
fig.add_trace(go.Scatter(x=anomaly_points_flow.index, y=anomaly_points_flow['Flow_Rate'], mode='markers', name='Anomaly Detected', marker=dict(color='purple')), row=3, col=1)
fig.add_trace(go.Scatter(x=leak_points_flow.index, y=leak_points_flow['Flow_Rate'], mode='markers', name='Leak Detected', marker=dict(color='green')), row=3, col=1)

fig.update_layout(height=1200, width=1200, title_text='Water Flow Data with Anomaly and Leak Detection', showlegend=True)
fig.show()
